<a href="https://colab.research.google.com/github/RenanBarreto4/Projects/blob/master/ProjetoCOVID(NAO_TERMINADO).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# ProjetoCOVID
### Feito por: Renan Barreto
### GitHub: https://github.com/RenanBarreto4
### Baixar Dataset: https://covid.saude.gov.br/

Este projeto tem como base analisar os dados disponíveis publicamente pelo governo brasileiro do impacto do Corona Vírus em nosso país. É uma recriação de meu primeiro projeto na ICMC Júnior, de forma atualizada, complementada e em python. Todos os gráficos foram feitos usando pacote de visualização interativa gráfica Plotly, então lembre sempre de interagir com os gráficos para obter mais informações.

Os principais tópicos a serem analisados serão:
*   Total de casos confirmados de todas as regiões do país;
*   Total de óbitos por região;
*   Gráficos com casos acumulados por região e país;
*   Gráficos com casos novos nas regiões e país;
*   Gráficos de óbitos por mês, de regiões do país e no Brasil todo
*   Mês em que mais houveram óbitos no país
*   Gráficos dos três estados com maior taxa de óbitos











Se estiver lendo esse notebook no GitHub, recomendo abri-lo no Google Colab (com o botão "Open in Colab" no início do projeto) ou baixá-lo e abrir em um Jupyter notebook para poder visualizar os gráficos que não aparecem.

In [ ]:
#importando bibliotecas para análise/manipulação
import pandas as pd
import numpy as np

In [ ]:
#importando plotly para visualização de gráficos
!pip3 install -U plotly
import plotly
import plotly.offline as py
import plotly.graph_objs as go

In [ ]:
#criando função para o plotly rodar em notebooks (vai precisar usar sempre plotly() quando for plotar)
def plotly():
  import IPython
  from plotly.offline import init_notebook_mode
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              plotly: 'https://cdn.plot.ly/plotly-1.5.1.min.js?noext',
            },
          });
        </script>
        '''))
  py.offline.init_notebook_mode(connected=True)

In [ ]:
#importando dados
covid_geral = pd.read_excel('HIST_PAINEL_COVIDBR_27jul2020.xlsx') 

In [ ]:
#tamanho do dataset
covid_geral.shape

(684502, 17)

In [ ]:
#analisando como é o dataset
covid_geral.head(175)   #157  310  3237  6775

regiao estado  ... emAcompanhamentoNovos  interior/metropolitana
0    Brasil    NaN  ...                   NaN                     NaN
1    Brasil    NaN  ...                   NaN                     NaN
2    Brasil    NaN  ...                   NaN                     NaN
3    Brasil    NaN  ...                   NaN                     NaN
4    Brasil    NaN  ...                   NaN                     NaN
..      ...    ...  ...                   ...                     ...
170   Norte     RO  ...                   NaN                     NaN
171   Norte     RO  ...                   NaN                     NaN
172   Norte     RO  ...                   NaN                     NaN
173   Norte     RO  ...                   NaN                     NaN
174   Norte     RO  ...                   NaN                     NaN

[175 rows x 17 columns]

In [ ]:
#analisando as últimas 7 colunas
covid_geral.tail(7)

regiao estado  ... emAcompanhamentoNovos  interior/metropolitana
684495  Centro-Oeste     DF  ...                   NaN                     1.0
684496  Centro-Oeste     DF  ...                   NaN                     1.0
684497  Centro-Oeste     DF  ...                   NaN                     1.0
684498  Centro-Oeste     DF  ...                   NaN                     1.0
684499  Centro-Oeste     DF  ...                   NaN                     1.0
684500  Centro-Oeste     DF  ...                   NaN                     1.0
684501  Centro-Oeste     DF  ...                   NaN                     1.0

[7 rows x 17 columns]

In [ ]:
#elimindando colunas desnecessárias
covid_geral.drop(columns=['coduf', 'codRegiaoSaude', 'nomeRegiaoSaude', 'emAcompanhamentoNovos'], inplace=True)

In [ ]:
#describe não ajuda muito nesse caso
covid_geral.describe()

codmun      semanaEpi  ...  Recuperadosnovos  interior/metropolitana
count  680190.000000  684502.000000  ...      1.000000e+02           677607.000000
mean   324362.542315      21.986051  ...      4.954565e+05                0.070067
std     98309.522822       5.096701  ...      4.912520e+05                0.255260
min    110000.000000       9.000000  ...      2.213000e+04                0.000000
25%    251110.000000      18.000000  ...      7.921525e+04                0.000000
50%    314468.500000      22.000000  ...      2.869960e+05                0.000000
75%    411710.000000      26.000000  ...      8.333535e+05                0.000000
max    530010.000000      31.000000  ...      1.667667e+06                1.000000

[8 rows x 8 columns]

In [ ]:
#filtrando uma região e tirando os dados que não preciso
#o dataset possui linhas que com a mesma região porém casos zerados, então retirei essas linhas com codmun nulo
covid_geral[(covid_geral.regiao == 'Sudeste')&(covid_geral.municipio.isnull())&(covid_geral.codmun.isnull())]

regiao estado  ... emAcompanhamentoNovos  interior/metropolitana
2618  Sudeste     MG  ...                   NaN                     NaN
2619  Sudeste     MG  ...                   NaN                     NaN
2620  Sudeste     MG  ...                   NaN                     NaN
2621  Sudeste     MG  ...                   NaN                     NaN
2622  Sudeste     MG  ...                   NaN                     NaN
...       ...    ...  ...                   ...                     ...
3229  Sudeste     SP  ...                   NaN                     NaN
3230  Sudeste     SP  ...                   NaN                     NaN
3231  Sudeste     SP  ...                   NaN                     NaN
3232  Sudeste     SP  ...                   NaN                     NaN
3233  Sudeste     SP  ...                   NaN                     NaN

[616 rows x 17 columns]

In [193]:
#criando um dataset sem as linhas nulas, porém sem região definida
covid_geral_null = covid_geral[(covid_geral.municipio.isnull())&(covid_geral.codmun.isnull())]

In [194]:
#criando datasets separados para cada região
covid_regiao_brasil = covid_geral_null[(covid_geral_null.regiao == 'Brasil')]
covid_regiao_nordeste = covid_geral_null[(covid_geral_null.regiao == 'Nordeste')]
covid_regiao_sudeste = covid_geral_null[(covid_geral_null.regiao == 'Sudeste')]
covid_regiao_sul = covid_geral_null[(covid_geral_null.regiao == 'Sul')]
covid_regiao_centro_oeste = covid_geral_null[(covid_geral_null.regiao == 'Centro-Oeste')]
covid_regiao_norte = covid_geral_null[(covid_geral_null.regiao == 'Norte')]

In [195]:
#obtendo total de casos e total de obitos de cada região
datasets = [covid_regiao_nordeste, covid_regiao_sudeste, covid_regiao_sul, covid_regiao_centro_oeste, covid_regiao_norte]
total_de_casos = []
total_de_obitos = []
for dataset in datasets:
  total_de_casos.append(dataset.casosNovos.sum())
print(total_de_casos)

for dataset in datasets:
  total_de_obitos.append(dataset.obitosNovos.sum())
print(total_de_obitos)

[795639, 837243, 198183, 223105, 388205]
[27592, 39449, 4238, 4683, 11656]


In [196]:
#criando uma lista com as regiões e paletas de cores
regioes = ['Nordeste', 'Sudeste', 'Sul', 'Centro-Oeste', 'Norte']
colors1 = ['#4169E1', '#6495ED', '#1E90FF', '#00BFFF', '#87CEFA']  #escala de cores azul
colors2 = ['#cccc00', '#ffff00', '#ffff40', '#ffff54', '#ffff94']  #escala de cores amarela

In [197]:
#gerando dois gráficos de barras para o total de casos e óbitos
from plotly.subplots import make_subplots   #importando método para gerar subplots
plotly()   #chamando a função

trace1 = go.Bar(x = regioes, y = total_de_casos, name = 'CASOS',marker = {'color': colors1})
trace2 = go.Bar(x = regioes, y = total_de_obitos, name = 'ÓBITOS', marker = {'color': colors2})  

fig = make_subplots(rows=1, cols=2,   #criando figura com 1 linha e 2 colunas
                    subplot_titles=['Total de Casos Por Região', 'Total de Óbitos por Região'])

fig.add_trace(trace1, row=1, col=1)   #adicionando trace1 na linha1, coluna1
fig.add_trace(trace2, row=1, col=2)   #adicionando trace2 na linha1, coluna2

fig.update_layout(#xaxis_title = 'Regiões',  #adicionando título ao eixo x
                  #yaxis_title = 'N° de Casos',   #adicionando título ao eixo y
                  yaxis_dtick = 75000,   #alterando quanto varia o eixo y no gráfico
                  font_size = 17,   #alterando tamanho de todos os textos
                  title_font_size = 35,   #alterando tamanho do título
                  xaxis_title_font_size = 23,   #alterando tamanho do título do eixo x
                  yaxis_title_font_size = 23)  #alterando tamanho do título do eixo y
                  

py.iplot(fig)   #plotando data

In [198]:
#criando um gráfico de pizza para a porcentagem de casos por região
plotly()   #chamando a função

trace = go.Pie(labels=regioes, values=total_de_casos, #labels define os setores; values define os dados;
               textinfo='label+percent',   #textinfo define as informações que vão aparecer no gráfico estático
               hoverinfo='label+value+percent',   #hoverinfo define o que aparece quando passa o mouse em cima;
               textfont=dict(size=21),   #textfont pode passar o tamnho da letra
               marker=dict(colors=colors1, line=dict(color='#ffffff', width=2)))  #marker serve para colocar a paleta de cores com colors; line modifica a linha entre os setores, pintando e aumentando a borda

fig = go.Figure([trace])  #criando uma figura com a lista dos trace

fig.update_layout(title = 'Porcentagem de Casos Por Região',
                  title_font_size = 35,
                  title_x = 0.47)

py.iplot(fig) #plotando o gráfico numa lista

In [199]:
#agrupando dataset por região e data, somando os valores e selecionando a coluna de casos acumulados
pd.DataFrame(covid_geral_null.groupby(['regiao','data']).sum()['casosAcumulado'])

casosAcumulado
regiao data                      
Brasil 2020-02-25               0
       2020-02-26               1
       2020-02-27               1
       2020-02-28               1
       2020-02-29               2
...                           ...
Sul    2020-07-23          179127
       2020-07-24          186283
       2020-07-25          192044
       2020-07-26          195729
       2020-07-27          198183

[924 rows x 1 columns]

In [200]:
#destacando os índices, transpondo o dataframe e eliminando o primeiro índice
df_acumulado = pd.DataFrame(covid_geral_null.groupby(['regiao','data']).sum()['casosAcumulado']).unstack().T.droplevel(level=0)
df_acumulado

regiao       Brasil  Centro-Oeste  Nordeste   Norte  Sudeste     Sul
data                                                                
2020-02-25        0             0         0       0        0       0
2020-02-26        1             0         0       0        1       0
2020-02-27        1             0         0       0        1       0
2020-02-28        1             0         0       0        1       0
2020-02-29        2             0         0       0        2       0
...             ...           ...       ...     ...      ...     ...
2020-07-23  2287475        200907    753593  373116   780732  179127
2020-07-24  2343366        207770    769743  378807   800763  186283
2020-07-25  2394513        212938    783343  383723   822465  192044
2020-07-26  2419091        217091    789896  386297   830078  195729
2020-07-27  2442375        223105    795639  388205   837243  198183

[154 rows x 6 columns]

In [201]:
#gráfico temporal de casos acumulados com filtro de tempo
plotly()

trace1 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Centro-Oeste'],  #definindo variáveis para x e y
                    name = 'Centro-Oeste',  #dando um nome para a legenda
                    line = dict(color=colors1[0]),  #colorindo a linha
                    opacity = 0.8)  #alterando a opacidade para 0.8

trace2 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Nordeste'],
                    name = 'Nordeste',
                    line = dict(color=colors1[1]),
                    opacity = 0.8)

trace3 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Norte'],
                    name = 'Norte',
                    line = dict(color=colors1[2]),
                    opacity = 0.8)

trace4 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Sudeste'],
                    name = 'Sudeste',
                    line = dict(color=colors1[3]),
                    opacity = 0.8)

trace5 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Sul'],
                    name = 'Sul',
                    line = dict(color=colors1[4]),
                    opacity = 0.8)

# trace6 = go.Scatter(x = df_acumulado.index, y = df_acumulado['Brasil'],
#                     name = 'Brasil',
#                     line = dict(color='#ffff00'),
#                     opacity = 0.8)

data = [trace1, trace2, trace3, trace4, trace5]#, trace6]

fig = go.Figure(data=data)

fig.update_xaxes(
    rangeslider_visible=True,   #cria um filtro de tempo
    rangeselector=dict(buttons=list([dict(count=1, label="1m", step="month", stepmode="backward"),   #cria botões de filtro de tempo
                                     dict(count=6, label="6m", step="month", stepmode="backward"),
                                     dict(count=1, label="YTD", step="year", stepmode="todate"),
                                     dict(count=1, label="1y", step="year", stepmode="backward"),
                                     dict(step="all")])),
    tickformatstops = [dict(dtickrange=[None, 1000], value="%H:%M:%S.%L ms"),   #conforme dá zoom, os nomes no eixo X fica do jeito que você quiser
                       dict(dtickrange=[1000, 60000], value="%H:%M:%S second"),
                       dict(dtickrange=[60000, 3600000], value="%H:%M minute"),
                       dict(dtickrange=[3600000, 86400000], value="%H:%M hour"),
                       dict(dtickrange=[86400000, 604800000], value="%e° %b day"),
                       dict(dtickrange=[604800000, "M1"], value="%e° %b week"),
                       dict(dtickrange=["M1", "M12"], value="%b %y"),
                       dict(dtickrange=["M12", None], value="%Y")])

fig.update_layout(title_text = 'Casos Acumulados ao Longo do Tempo Por Região',
                  title_font_size = 30,
                  title_x = 0.5,
                  xaxis_gridcolor = "#eee",
                  yaxis_gridcolor = "#eee",
                  plot_bgcolor="#fff")   #alterando cor entre os eixos

py.iplot(fig)

In [202]:
#gráfico de barras com os casos acumulados por região
from plotly.subplots import make_subplots 

plotly()

trace1 = go.Bar(x = covid_regiao_centro_oeste.data, y = covid_regiao_centro_oeste.casosAcumulado, name = 'Centro-Oeste', hoverinfo='y')
trace2 = go.Bar(x = covid_regiao_nordeste.data, y = covid_regiao_nordeste.casosAcumulado, name = 'Nordeste', hoverinfo='y')
trace3 = go.Bar(x = covid_regiao_norte.data, y = covid_regiao_norte.casosAcumulado, name = 'Norte', hoverinfo='y')
trace4 = go.Bar(x = covid_regiao_sudeste.data, y = covid_regiao_sudeste.casosAcumulado, name = 'Sudeste', hoverinfo='y')
trace5 = go.Bar(x = covid_regiao_sul.data, y = covid_regiao_sul.casosAcumulado, name = 'Sul', hoverinfo='y')
#trace6 = go.Bar(x = covid_regiao_brasil.data, y = covid_regiao_brasil.casosAcumulado, name = 'Brasil', hoverinfo='y')

fig = make_subplots(rows=3, cols=2,  
                    subplot_titles=['Centro-Oeste','Nordeste','Norte','Sudeste','Sul'],   #atribuindo um subtítulo
                    shared_yaxes=True)   #compartilhando o eixo y com os gráficos da mesma linha

fig.add_trace(trace1, row=1, col=1)   #adicionando trace1 na linha1, coluna1
fig.add_trace(trace2, row=1, col=2)   #adicionando trace2 na linha1, coluna2
fig.add_trace(trace3, row=2, col=1)
fig.add_trace(trace4, row=2, col=2)
fig.add_trace(trace5, row=3, col=1)
#fig.add_trace(trace6, row=3, col=2)  #colocar o brasil tirando a #

fig.update_layout(title = 'Casos Acumulados ao Longo do Tempo Por Região',  #adicionando título
                  font_size = 17,   #alterando tamanho de todos os textos
                  title_font_size = 30,   #alterando tamanho do título
                  #yaxis_title = 'N° de Casos',  #alterando o título do eixo y
                  xaxis_title_font_size = 25,   #alterando tamanho do título do eixo x
                  yaxis_title_font_size = 25,  #alterando tamanho do título do eixo y
                  #yaxis_dtick = 50000,   #alterando quanto varia o eixo y no gráfico
                  title_x = 0.5)   #colocando o título no meio

py.iplot(fig)

In [203]:
#mesmo dataframe para os casos novos
df_novos = pd.DataFrame(covid_geral_null.groupby(['regiao','data']).sum()['casosNovos']).unstack().T.droplevel(level=0)
df_novos

regiao      Brasil  Centro-Oeste  Nordeste  Norte  Sudeste   Sul
data                                                            
2020-02-25       0             0         0      0        0     0
2020-02-26       1             0         0      0        1     0
2020-02-27       0             0         0      0        0     0
2020-02-28       0             0         0      0        0     0
2020-02-29       1             0         0      0        1     0
...            ...           ...       ...    ...      ...   ...
2020-07-23   59961          8161     18336   6659    20234  6571
2020-07-24   55891          6863     16150   5691    20031  7156
2020-07-25   51147          5168     13600   4916    21702  5761
2020-07-26   24578          4153      6553   2574     7613  3685
2020-07-27   23284          6014      5743   1908     7165  2454

[154 rows x 6 columns]

In [204]:
#gráfico temporal de casos novos
plotly()

trace1 = go.Scatter(x = df_novos.index, y = df_novos['Centro-Oeste'],  #definindo variáveis para x e y
                    name = 'Centro-Oeste',  #dando um nome para a legenda
                    line = dict(color=colors1[0]),  #colorindo a linha
                    opacity = 0.8)  #alterando a opacidade para 0.8

trace2 = go.Scatter(x = df_novos.index, y = df_novos['Nordeste'],
                    name = 'Nordeste',
                    line = dict(color=colors1[1]),
                    opacity = 0.8)

trace3 = go.Scatter(x = df_novos.index, y = df_novos['Norte'],
                    name = 'Norte',
                    line = dict(color=colors1[2]),
                    opacity = 0.8)

trace4 = go.Scatter(x = df_novos.index, y = df_novos['Sudeste'],
                    name = 'Sudeste',
                    line = dict(color=colors1[3]),
                    opacity = 0.8)

trace5 = go.Scatter(x = df_novos.index, y = df_novos['Sul'],
                    name = 'Sul',
                    line = dict(color=colors1[4]),
                    opacity = 0.8)

fig = make_subplots(rows=3, cols=2, 
                    subplot_titles=['Centro-Oeste','Nordeste','Norte','Sudeste','Sul'],   #atribuindo um subtítulo
                    shared_yaxes=True)

fig.add_trace(trace1, row=1, col=1)   #adicionando trace1 na linha1, coluna1
fig.add_trace(trace2, row=1, col=2)   
fig.add_trace(trace3, row=2, col=1)
fig.add_trace(trace4, row=2, col=2)
fig.add_trace(trace5, row=3, col=1)

fig.update_layout(title_text = 'Casos Novos ao Longo do Tempo Por Região',
                  title_font_size = 30,
                  title_x = 0.5)

py.iplot(fig)

In [292]:
#gráfico temporal de casos novos e acumulados do Brasil todo
plotly()

trace1 = go.Bar(x = covid_regiao_brasil.data, y = covid_regiao_brasil.casosAcumulado, name = 'Brasil', marker = {'color' : '#ffff00'})

trace2 = go.Scatter(x = df_novos.index, y = df_novos['Brasil'], name = 'Brasil', line = dict(color='#ffff00'), opacity = 0.8)

fig = make_subplots(rows=1, cols=2,  subplot_titles=['Casos Acumulados','Casos por Dia'])

fig.add_trace(trace1, row=1, col=1)
fig.add_trace(trace2, row=1, col=2)

fig.update_xaxes(
    rangeslider_visible=True,   #cria um filtro de tempo
    rangeselector=dict(buttons=list([dict(count=1, label="1m", step="month", stepmode="backward"),   #cria botões de filtro de tempo
                                     dict(count=6, label="6m", step="month", stepmode="backward"),
                                     dict(count=1, label="YTD", step="year", stepmode="todate"),
                                     dict(count=1, label="1y", step="year", stepmode="backward"),
                                     dict(step="all")])),
    tickformatstops = [dict(dtickrange=[None, 1000], value="%H:%M:%S.%L ms"),   #conforme dá zoom, os nomes no eixo X fica do jeito que você quiser
                       dict(dtickrange=[1000, 60000], value="%H:%M:%S second"),
                       dict(dtickrange=[60000, 3600000], value="%H:%M minute"),
                       dict(dtickrange=[3600000, 86400000], value="%H:%M hour"),
                       dict(dtickrange=[86400000, 604800000], value="%e° %b day"),
                       dict(dtickrange=[604800000, "M1"], value="%e° %b week"),
                       dict(dtickrange=["M1", "M12"], value="%b %y"),
                       dict(dtickrange=["M12", None], value="%Y")])

fig.update_layout(title_text = 'Casos Acumulados e Novos do Brasil Todo',
                  title_font_size = 30, 
                  plot_bgcolor="#fff", 
                  #xaxis_gridcolor = "#eee",
                  #yaxis_gridcolor = "#eee",
                  showlegend = False,
                  title_x = 0.5)


py.iplot(fig)

In [206]:
#criando dataframes separados por mês
covid_geral_null.set_index('regiao', inplace = True)   #colocando a região como índice para facilitar a seleção
covid_geral_marco = covid_geral_null.loc[(covid_geral_null.data >= '2020-03-01')&(covid_geral_null.data <= '2020-03-31')]
covid_geral_abril = covid_geral_null.loc[(covid_geral_null.data >= '2020-04-01')&(covid_geral_null.data <= '2020-04-30')]
covid_geral_maio = covid_geral_null.loc[(covid_geral_null.data >= '2020-05-01')&(covid_geral_null.data <= '2020-05-31')]
covid_geral_junho = covid_geral_null.loc[(covid_geral_null.data >= '2020-06-01')&(covid_geral_null.data <= '2020-06-30')]
covid_geral_julho = covid_geral_null.loc[(covid_geral_null.data >= '2020-07-01')&(covid_geral_null.data <= '2020-07-27')]

In [207]:
#visulização de como ficou o dataframe
covid_geral_marco

estado municipio  ...  emAcompanhamentoNovos  interior/metropolitana
regiao                         ...                                               
Brasil          NaN       NaN  ...                    NaN                     NaN
Brasil          NaN       NaN  ...                    NaN                     NaN
Brasil          NaN       NaN  ...                    NaN                     NaN
Brasil          NaN       NaN  ...                    NaN                     NaN
Brasil          NaN       NaN  ...                    NaN                     NaN
...             ...       ...  ...                    ...                     ...
Centro-Oeste     DF       NaN  ...                    NaN                     NaN
Centro-Oeste     DF       NaN  ...                    NaN                     NaN
Centro-Oeste     DF       NaN  ...                    NaN                     NaN
Centro-Oeste     DF       NaN  ...                    NaN                     NaN
Centro-Oeste     DF       NaN  ...                    NaN                     NaN

[868 rows x 16 columns]

In [338]:
#teste para soma de casos em um mês dada uma região
covid_geral_marco.loc['Brasil','casosNovos'].sum()

5715

In [331]:
#somando todos os casos e colocando numa lista de listas com cada uma sendo todas as regiões em certo mês
regioes = ['Nordeste', 'Sudeste', 'Sul', 'Centro-Oeste', 'Norte', 'Brasil']
meses = ['marco','abril','maio','junho','julho']
marco = []
abril = []
maio = []
junho = []
julho = []
casos_por_mes = [marco,abril,maio,junho,julho]
datasets2 = [covid_geral_marco,covid_geral_abril,covid_geral_maio,covid_geral_junho,covid_geral_julho]

for i in regioes:
  for j in range(len(meses)):
    casos_por_mes[j].append(datasets2[j].loc[i,'casosNovos'].sum())

casos_por_mes

[[875, 3404, 672, 470, 294, 5715],
 [23643, 39037, 4286, 2219, 10478, 79663],
 [154234, 144797, 18098, 14711, 96980, 428820],
 [301602, 298645, 53116, 79800, 154678, 887841],
 [315285, 351358, 122011, 125905, 125775, 1040334]]

In [332]:
#transpondo matriz para ter em cada lista só uma região e todos os meses
casos_por_mes2 = np.array(casos_por_mes).T.tolist()
casos_por_mes2

[[875, 23643, 154234, 301602, 315285],
 [3404, 39037, 144797, 298645, 351358],
 [672, 4286, 18098, 53116, 122011],
 [470, 2219, 14711, 79800, 125905],
 [294, 10478, 96980, 154678, 125775],
 [5715, 79663, 428820, 887841, 1040334]]

In [333]:
#gráfico de barras do número de casos por região e mês
plotly()

trace1 = go.Bar(x = meses, y = casos_por_mes2[0], name = 'Nordeste', marker = {'color': colors1[0]}, hoverinfo = 'y+name')
trace2 = go.Bar(x = meses, y = casos_por_mes2[1], name = 'Sudeste', marker = {'color': colors1[1]}, hoverinfo = 'y+name')  
trace3 = go.Bar(x = meses, y = casos_por_mes2[2], name = 'Sul', marker = {'color': colors1[2]}, hoverinfo = 'y+name')  
trace4 = go.Bar(x = meses, y = casos_por_mes2[3], name = 'Centro-Oeste', marker = {'color': colors1[3]}, hoverinfo = 'y+name')
trace5 = go.Bar(x = meses, y = casos_por_mes2[4], name = 'Norte', marker = {'color': colors1[4]}, hoverinfo = 'y+name')
trace6 = go.Bar(x = meses, y = casos_por_mes2[5], name = 'Brasil', marker = {'color': colors2[1]}, hoverinfo = 'y+name')


data = [trace1, trace2, trace3, trace4, trace5, trace6]

fig = go.Figure(data=data)

fig.update_layout(barmode='group', #alterando o layout para barras agrupadas com o método Layout, o que já é o padrão (então esse comando é desnecessário)
                  title = 'Total de Casos Por Região/Mês',
                  xaxis_title = 'Meses',
                  yaxis_title = 'N° de Casos',
                  font_size = 17,
                  title_font_size = 35,
                  xaxis_title_font_size = 25,
                  yaxis_title_font_size = 25,
                  title_x = 0.5,
                  plot_bgcolor="#fff", 
                  xaxis_gridcolor = "#eee",
                  yaxis_gridcolor = "#eee")

py.iplot(fig)

In [335]:
#mesma manipulação, mas para óbitos novos
regioes = ['Nordeste', 'Sudeste', 'Sul', 'Centro-Oeste', 'Norte', 'Brasil']
marco2 = []
abril2 = []
maio2 = []
junho2 = []
julho2 = []
casos_por_mes3 = [marco2,abril2,maio2,junho2,julho2]
datasets2 = [covid_geral_marco,covid_geral_abril,covid_geral_maio,covid_geral_junho,covid_geral_julho]

for i in regioes:
  for j in range(len(meses)):
    casos_por_mes3[j].append(datasets2[j].loc[i,'obitosNovos'].sum())

casos_por_mes4 = np.array(casos_por_mes3).T.tolist()
casos_por_mes4

[[22, 1514, 7330, 10412, 8314],
 [161, 3233, 10440, 13622, 11993],
 [9, 171, 369, 1055, 2634],
 [5, 74, 296, 1355, 2953],
 [4, 708, 4978, 3836, 2130],
 [201, 5700, 23413, 30280, 28024]]

In [339]:
#gráfico de barras do número de obitos por região e mês
plotly()

trace1 = go.Bar(x = meses, y = casos_por_mes4[0], name = 'Nordeste', marker = {'color': colors1[0]}, hoverinfo = 'y+name')
trace2 = go.Bar(x = meses, y = casos_por_mes4[1], name = 'Sudeste', marker = {'color': colors1[1]}, hoverinfo = 'y+name')  
trace3 = go.Bar(x = meses, y = casos_por_mes4[2], name = 'Sul', marker = {'color': colors1[2]}, hoverinfo = 'y+name')  
trace4 = go.Bar(x = meses, y = casos_por_mes4[3], name = 'Centro-Oeste', marker = {'color': colors1[3]}, hoverinfo = 'y+name')
trace5 = go.Bar(x = meses, y = casos_por_mes4[4], name = 'Norte', marker = {'color': colors1[4]}, hoverinfo = 'y+name')
trace6 = go.Bar(x = meses, y = casos_por_mes4[5], name = 'Brasil', marker = {'color': colors2[1]}, hoverinfo = 'y+name')


data = [trace1, trace2, trace3, trace4, trace5, trace6]

fig = go.Figure(data=data)

fig.update_layout(barmode='group',
                  title = 'Total de Óbitos Por Região/Mês',
                  xaxis_title = 'Meses',
                  yaxis_title = 'N° de Óbitos',
                  font_size = 17,
                  title_font_size = 35,
                  xaxis_title_font_size = 25,
                  yaxis_title_font_size = 25,
                  title_x = 0.5,
                  plot_bgcolor="#fff", 
                  xaxis_gridcolor = "#eee",
                  yaxis_gridcolor = "#eee")

py.iplot(fig)

In [431]:
df_novos_obitos = pd.DataFrame(covid_geral_null.groupby(['estado','data']).sum()['obitosAcumulado']).unstack().T.droplevel(level=0)
df_max = df_novos_obitos.iloc[-1]
pd.DataFrame(df_max).T

estado       AC    AL    AM   AP    BA    CE  ...   RR    RS   SC    SE     SP   TO
2020-07-27  493  1514  3224  556  3227  7509  ...  474  1611  924  1340  21676  350

[1 rows x 27 columns]

In [435]:
import heapq
maiores_estados = df_max.tolist()
heapq.nlargest(3,maiores_estados)

[21676, 12876, 7509]

In [439]:
#recriando os datasets para colocar o estado como índice
covid_geral_null2 = covid_geral[(covid_geral.municipio.isnull())&(covid_geral.codmun.isnull())]
covid_geral_null2.set_index('estado', inplace = True)
covid_geral_marco2 = covid_geral_null2.loc[(covid_geral_null2.data >= '2020-03-01')&(covid_geral_null2.data <= '2020-03-31')]
covid_geral_abril2 = covid_geral_null2.loc[(covid_geral_null2.data >= '2020-04-01')&(covid_geral_null2.data <= '2020-04-30')]
covid_geral_maio2 = covid_geral_null2.loc[(covid_geral_null2.data >= '2020-05-01')&(covid_geral_null2.data <= '2020-05-31')]
covid_geral_junho2 = covid_geral_null2.loc[(covid_geral_null2.data >= '2020-06-01')&(covid_geral_null2.data <= '2020-06-30')]
covid_geral_julho2 = covid_geral_null2.loc[(covid_geral_null2.data >= '2020-07-01')&(covid_geral_null2.data <= '2020-07-27')]

In [449]:
estados_obitos = ['CE', 'RJ', 'SP']
marco3 = []
abril3 = []
maio3 = []
junho3 = []
julho3 = []
casos_por_mes5 = [marco3,abril3,maio3,junho3,julho3]
datasets3 = [covid_geral_marco2,covid_geral_abril2,covid_geral_maio2,covid_geral_junho2,covid_geral_julho2]

for i in estados_obitos:
  for j in range(len(meses)):
    casos_por_mes5[j].append(datasets3[j].loc[i,'obitosNovos'].sum())

casos_por_mes6 = np.array(casos_por_mes5).T.tolist()
casos_por_mes6

[[7, 475, 2528, 3136, 1363],
 [23, 831, 4490, 4736, 2796],
 [136, 2239, 5240, 7148, 6913]]

In [455]:
#gráfico de barras do número de obitos por região e mês
plotly()

trace1 = go.Bar(x = meses, y = casos_por_mes6[0], name = 'Ceará', marker = {'color': colors1[0]}, hoverinfo = 'y+name')
trace2 = go.Bar(x = meses, y = casos_por_mes6[1], name = 'Rio De Janeiro', marker = {'color': colors1[1]}, hoverinfo = 'y+name')  
trace3 = go.Bar(x = meses, y = casos_por_mes6[2], name = 'São Paulo', marker = {'color': colors1[2]}, hoverinfo = 'y+name')  



data = [trace1, trace2, trace3]

fig = go.Figure(data=data)

fig.update_layout(barmode='group',
                  title = 'Total de Óbitos Nos 3 Estados Mais Afetados Por Mês',
                  xaxis_title = 'Meses',
                  yaxis_title = 'N° de Óbitos',
                  font_size = 17,
                  title_font_size = 35,
                  xaxis_title_font_size = 25,
                  yaxis_title_font_size = 25,
                  title_x = 0.5,
                  plot_bgcolor="#fff", 
                  xaxis_gridcolor = "#eee",
                  yaxis_gridcolor = "#eee")

py.iplot(fig)

In [458]:
df_acumulado2 = df_acumulado.drop(columns='Brasil')
df_acumulado2

regiao      Centro-Oeste  Nordeste   Norte  Sudeste     Sul
data                                                       
2020-02-25             0         0       0        0       0
2020-02-26             0         0       0        1       0
2020-02-27             0         0       0        1       0
2020-02-28             0         0       0        1       0
2020-02-29             0         0       0        2       0
...                  ...       ...     ...      ...     ...
2020-07-23        200907    753593  373116   780732  179127
2020-07-24        207770    769743  378807   800763  186283
2020-07-25        212938    783343  383723   822465  192044
2020-07-26        217091    789896  386297   830078  195729
2020-07-27        223105    795639  388205   837243  198183

[154 rows x 5 columns]

In [461]:
#instalando e importando bar_chart_race
!pip install -U bar_chart_race
import bar_chart_race as bcr

Requirement already up-to-date: bar_chart_race in /usr/local/lib/python3.6/dist-packages (0.1.0)


In [462]:
#criando bar chart race para os casos acumulados por região
bcr.bar_chart_race(df_acumulado2, title = 'Número de Casos Acumulados de COVID-19 por Região', 
                   period_length=300, period_fmt='%b %-d, %Y',perpendicular_bar_func='mean')

In [463]:
#criando bar chart race para os casos acumulados por estado
bcr.bar_chart_race(df_novos_obitos, title = 'Número de Casos Acumulados de COVID-19 por Estado', 
                   period_length=300, period_fmt='%b %-d, %Y',perpendicular_bar_func='mean', n_bars = 20)

/usr/local/lib/python3.6/dist-packages/bar_chart_race/_make_chart.py:226: UserWarning:

Some of your columns never make an appearance in the animation. To reduce color repetition, set `filter_column_colors` to `True`

